## Install libs

In [ ]:
!pip install uv

In [ ]:
!uv pip install .

## Imports

In [ ]:
%load_ext autoreload
%autoreload 2

In [ ]:
import os
import sys

sys.path.append(os.path.dirname(os.getcwd()))
# sys.path

In [ ]:
import all_need_funcs

In [ ]:
from tinkoff.invest import Client
from tinkoff.invest.constants import INVEST_GRPC_API
from copy import deepcopy
import numpy as np
import pandas as pd

In [ ]:
from catboost import CatBoostRegressor
from sklearn.model_selection import train_test_split, GridSearchCV
# Вычисляем MSE для каждого набора данных
from sklearn.metrics import mean_squared_error
import matplotlib.pyplot as plt
from IPython.display import clear_output
from time import sleep
from sklearn.metrics import mean_squared_error, mean_absolute_percentage_error

In [ ]:
from prophet import Prophet

# from pmdarima import auto_arima

from statsmodels.tsa.statespace.sarimax import SARIMAX

import os
import pickle
from catboost import CatBoostRegressor
from tqdm import tqdm


In [ ]:
T_TOKEN = "t..."
T_TOKEN

## Try to get data

### Tinkoff

#### Отдельные функции - обучение

#### Всё сразу

In [ ]:
res_df, scalers = all_need_funcs.create_featured_data_frame(all_need_funcs.get_symbol_data,
                                               interval="1d",
                                               token=T_TOKEN,
                                               symbols_list=all_need_funcs.RUS_PROD_TICKERS_12,
                                            #    symbols_list=["SBER", "YDEX", "T"],
                                               t_token=T_TOKEN,
                                              #  target_scaler='min-max'
                                               )

In [ ]:
# res_df['Date'].max()
res_df['target'].min(), res_df['target'].max()

In [ ]:
cur_target_col = "target"
cur_target_col

In [ ]:
res_df.sort_values(by=['Symbol', 'Date'])[['Date', 'Symbol', 'target', 'scaled_Close']].head(20)
cur_df = res_df[res_df['Symbol'] == 'SBER']
cur_df['target'][:100].plot()
cur_df['scaled_Close'][:100].plot()
plt.legend()
plt.show()


In [ ]:
train_df, val_df, test_df = all_need_funcs.split_df_by_dates(res_df,
                                                             train_start_date="2021-01-01"
                                                             )

X_train, y_train = all_need_funcs.create_X_y_df_from_df(train_df, target_col=cur_target_col)
X_val, y_val = all_need_funcs.create_X_y_df_from_df(val_df, target_col=cur_target_col)
X_test, y_test = all_need_funcs.create_X_y_df_from_df(test_df, target_col=cur_target_col)

X_train.shape, y_train.shape, X_val.shape, y_val.shape, X_test.shape, y_test.shape
# X_train.columns.tolist()
print(train_df['Symbol'].unique())
print(val_df['Symbol'].unique())
print(test_df['Symbol'].unique())


print(len(train_df['Symbol'].unique()))
print(len(val_df['Symbol'].unique()))
print(len(test_df['Symbol'].unique()))

In [ ]:
train_df['Date'].min()

In [ ]:
train_dict = all_need_funcs.create_grouped_X_y_df_from_df(train_df, target_col=cur_target_col)
val_dict = all_need_funcs.create_grouped_X_y_df_from_df(val_df, target_col=cur_target_col)
test_dict = all_need_funcs.create_grouped_X_y_df_from_df(test_df, target_col=cur_target_col)

In [ ]:
len(train_dict.keys())
# len(val_dict.keys())
# len(test_dict.keys())

train_dict['SBER'][0].shape
# train_dict['SBER'][1].min()

##### Проверка на стационарность

In [ ]:
res_df, scalers = all_need_funcs.create_featured_data_frame(all_need_funcs.get_symbol_data,
                                               interval="1d",
                                               token=T_TOKEN,
                                               symbols_list=all_need_funcs.RUS_PROD_TICKERS_12,
                                            #    symbols_list=["SBER", "YDEX", "T"],
                                               t_token=T_TOKEN,
                                               )

In [ ]:
res_df[res_df['Symbol'] == 'SIBN']['diff_target'].plot(label='SIBN', alpha=0.5)
res_df[res_df['Symbol'] == 'SBER']['diff_target'].plot(label='SBER', alpha=0.5)
res_df[res_df['Symbol'] == 'T']['diff_target'].plot(label='T', alpha=0.5)
res_df[res_df['Symbol'] == 'YDEX']['diff_target'].plot(label='YDEX', alpha=0.5)
plt.legend()
plt.show()

In [ ]:
# Проверяем стационарность для разных символов
symbols_to_check = ['SIBN', 'SBER', 'T', 'YDEX']

print("ПРОВЕРКА СТАЦИОНАРНОСТИ ДИФФЕРЕНЦИРОВАННЫХ ДАННЫХ (diff_target):")
print("="*80)
for symbol in symbols_to_check[:1]:
    symbol_data = res_df[res_df['Symbol'] == symbol]['diff_target']
    if len(symbol_data.dropna()) > 0:
        all_need_funcs.comprehensive_stationarity_test(symbol_data, f'{symbol} diff_target')

print("\n\nПРОВЕРКА СТАЦИОНАРНОСТИ ИСХОДНЫХ ЦЕН ЗАКРЫТИЯ:")
print("="*80)
for symbol in symbols_to_check[:1]:
    symbol_data = res_df[res_df['Symbol'] == symbol]['Close']
    if len(symbol_data.dropna()) > 0:
        all_need_funcs.comprehensive_stationarity_test(symbol_data, f'{symbol} Close')


##### CatBoost - help func

In [ ]:
# X_train.columns.tolist()
X_train, y_train
cur_sym = 'SBER'

cur_train_df = train_df[train_df['Symbol'] == cur_sym]
cur_val_df = val_df[val_df['Symbol'] == cur_sym]
cur_test_df = test_df[test_df['Symbol'] == cur_sym]

X_train, y_train = all_need_funcs.create_X_y_df_from_df(cur_train_df, target_col='diff_target')
X_val, y_val = all_need_funcs.create_X_y_df_from_df(cur_val_df, target_col='diff_target')
X_test, y_test = all_need_funcs.create_X_y_df_from_df(cur_test_df, target_col='diff_target')

X_train.shape, y_train.shape, X_val.shape, y_val.shape, X_test.shape, y_test.shape

In [ ]:
all_need_funcs.train_simple_cbt(X_train, y_train, X_val, y_val, X_test, y_test,
                 cbt_params={
                     'iterations': 500,
                     'depth': 5,
                     'learning_rate': 0.001,
                     'l2_leaf_reg': 0.2,
                     'loss_function': 'RMSE',
                     'random_seed': 42,
                     'verbose': 100,
                     'task_type': 'GPU',
                 },
                 do_plot=True)


In [ ]:
all_need_funcs.train_simple_cbt(X_train, y_train, X_val, y_val, X_test, y_test,
                 cbt_params={
                     'iterations': 1000,
                     'depth': 5,
                     'learning_rate': 0.001,
                     'l2_leaf_reg': 0.2,
                     'loss_function': 'RMSE',
                     'random_seed': 42,
                     'verbose': 100,
                     'task_type': 'GPU',
                 },
                 do_plot=True)


In [ ]:
all_need_funcs.train_simple_cbt(X_train, y_train, X_val, y_val, X_test, y_test,
                 cbt_params={
                     'iterations': 2000,
                     'depth': 5,
                     'learning_rate': 0.001,
                     'l2_leaf_reg': 0.2,
                     'loss_function': 'RMSE',
                     'random_seed': 42,
                     'verbose': 100,
                     'task_type': 'GPU',
                 },
                 do_plot=True)


In [ ]:
all_need_funcs.train_simple_cbt(X_train, y_train, X_val, y_val, X_test, y_test,
                 cbt_params={
                     'iterations': 5000,
                     'depth': 5,
                     'learning_rate': 0.001,
                     'l2_leaf_reg': 0.2,
                     'loss_function': 'RMSE',
                     'random_seed': 42,
                     'verbose': 100,
                     'task_type': 'GPU',
                 },
                 do_plot=True)


In [ ]:
all_need_funcs.train_simple_cbt(X_train, y_train, X_val, y_val, X_test, y_test,
                 cbt_params={
                     'iterations': 20000,
                     'depth': 5,
                     'learning_rate': 0.001,
                     'l2_leaf_reg': 0.2,
                     'loss_function': 'RMSE',
                     'random_seed': 42,
                     'verbose': 100,
                     'task_type': 'GPU',
                 },
                 do_plot=True)


In [ ]:
rs_model = all_need_funcs.random_search_catboost(X_train, y_train,
                                                  X_val, y_val,
                                                  X_test, y_test,
                                                  n_iter=4,
                                                  random_state=42,
                                                  use_gpu=True,
                                                  rs_verbose=10,
                                                  cbt_verbose=1)

In [ ]:
rs_model

In [ ]:
rs_model.get_evals_result().keys()

In [ ]:
all_need_funcs.estimate_best_model(rs_model, X_train, y_train, X_val, y_val, X_test, y_test)


##### CatBoost - for each company

In [ ]:
syms = list(train_dict.keys())
res_cbts = {}
for sym in tqdm(syms[:]):
    # print(f"Training {sym}")
    X_train, y_train = train_dict[sym]
    X_val, y_val = val_dict[sym]
    X_test, y_test = test_dict[sym]

    # model = all_need_funcs.train_simple_cbt(X_train, y_train, X_val, y_val, X_test, y_test,
    #                          cbt_params={
    #                              'iterations': 500,
    #                              'depth': 10,
    #                              'learning_rate': 0.005,
    #                              'l2_leaf_reg': 0.2,
    #                              'loss_function': 'RMSE',
    #                              'random_seed': 42,
    #                              'verbose': 0,
    #                              'task_type': 'GPU'
    #                          },)
    model = all_need_funcs.random_search_catboost(X_train, y_train,
                                                  X_val, y_val,
                                                  X_test, y_test,
                                                  n_iter=8,
                                                  random_state=42,
                                                  use_gpu=True,
                                                  rs_verbose=10,
                                                  cbt_verbose=1)
    res_cbts[sym] = model

    clear_output(wait=True)


In [ ]:
res_cbts
# test_dict

In [ ]:
do_pred_diff_target = (cur_target_col == "target")
do_pred_diff_target

In [ ]:
all_need_funcs.eval_cbts_on_test(res_cbts, scalers, train_df,
                                 do_pred_diff_target=do_pred_diff_target,
                                  # do_scale=False,
                                 sleep_time=1,
                                 y_col='target')

In [ ]:
all_need_funcs.eval_cbts_on_test(res_cbts, scalers, test_df,
                                 do_pred_diff_target=do_pred_diff_target,
                                  # do_scale=False,
                                 sleep_time=1,
                                 y_col='target')

In [ ]:
train_df.sort_values(by=['Symbol', 'Date'])[['Date', 'Symbol', 'target', 'scaled_Close']].tail(20)
train_df['scaled_Close'][:100].plot()
train_df['target'][:100].plot()
plt.legend()
plt.show()


##### save CatBoosts

In [ ]:
# Создаем директорию для сохранения моделей CatBoost, если она не существует
saving_dir = "./checkpoints_MinMaxScaler_target/catboosts"
os.makedirs(saving_dir, exist_ok=True)

# Сохраняем каждую модель CatBoost в отдельный файл
for ticker, model in res_cbts.items():
    model_path = f"{saving_dir}/{ticker}_catboost.cbm"
    if os.path.exists(model_path):
        os.remove(model_path)
    model.save_model(model_path)
    print(f"Модель CatBoost для {ticker} сохранена в {model_path}")
    # print(f"Модель CatBoost {model.get_params()}")

# print(f"Модели CatBoost успешно сохранены в директории 'checkpoints/catboosts'")

In [ ]:
# Создаем директорию для сохранения скейлеров, если она не существует
saving_dir = "./checkpoints_MinMaxScaler_target/scalers"
os.makedirs(saving_dir, exist_ok=True)

# Сохраняем каждый скейлер в отдельный файл
for ticker, scaler in scalers.items():
    scaler_path = f"{saving_dir}/{ticker}_scaler.pkl"
    if os.path.exists(scaler_path):
        os.remove(scaler_path)
    with open(scaler_path, 'wb') as f:
        pickle.dump(scaler, f)
    # print(f"{ticker} : mean = {scaler.mean_[0]:.1f} | scale = {scaler.scale_[0]:.1f} | path = {scaler_path}")

print(f"Скейлеры успешно сохранены в директории 'checkpoints/scalers'")


In [ ]:
# !zip -r ./checkpoints.zip ./checkpoints
!zip -r ./checkpoints_MinMaxScaler_target.zip ./checkpoints_MinMaxScaler_target

In [ ]:
from google.colab import files
files.download(f"./checkpoints_MinMaxScaler_target.zip")

In [ ]:
files.download(f"./checkpoints_MinMaxScaler_target.zip")

In [ ]:
saving_dir = "./checkpoints_MinMaxScaler_target/catboosts"
# Загружаем модели CatBoost из файлов
loaded_models = {}
for file_name in os.listdir(saving_dir):
    ticker = file_name.split("_")[0]
    model_path = f"{saving_dir}/{file_name}"
    if os.path.exists(model_path):
        model = CatBoostRegressor()
        model.load_model(model_path)
        loaded_models[ticker] = model
        print(f"Модель CatBoost для {ticker} загружена из {model_path}")

print(f"Загружено {len(loaded_models)} моделей CatBoost из директории 'checkpoints/catboosts'")

In [ ]:
# # Выводим словарь с моделями
# res_cbts['CHMF'].feature_importances_
# res_cbts['SBER'].predict(test_dict['SBER',][0])


In [ ]:
loaded_models['CHMF'].get_feature_importance()

In [ ]:
len(res_cbts.keys())

# res_cbts['SBER'].feature_importances_
# res_cbts['SBER'].get_metadata
# X_train.columns.tolist()

In [ ]:
# Создаем директорию для сохранения скейлеров, если она не существует
saving_dir = "../checkpoints/scalers"
os.makedirs(saving_dir, exist_ok=True)


In [ ]:
# Сохраняем каждый скейлер в отдельный файл
for ticker, scaler in scalers.items():
    scaler_path = f"{saving_dir}/{ticker}_scaler.pkl"
    if os.path.exists(scaler_path):
        os.remove(scaler_path)
    with open(scaler_path, 'wb') as f:
        pickle.dump(scaler, f)
    print(f"{ticker} : mean = {scaler.mean_[0]:.1f} | scale = {scaler.scale_[0]:.1f} | path = {scaler_path}")

print(f"Скейлеры успешно сохранены в директории 'checkpoints/scalers'")


In [ ]:
os.getcwd()
saved_scalers = {}
for file_name in os.listdir(saving_dir):
    ticker = file_name.split("_")[0]
    scaler_path = f"{saving_dir}/{file_name}"
    # print(scaler_path)
    with open(scaler_path, 'rb') as f:
        scaler = pickle.load(f)

    saved_scalers[ticker] = scaler
    print(f"{ticker} : mean = {scaler.mean_[0]:.1f} | scale = {scaler.scale_[0]:.1f}")


In [ ]:
saved_scalers['T'].mean_, saved_scalers['T'].scale_

In [ ]:
scalers['T'].mean_, scalers['T'].scale_

In [ ]:
# try to make predict

##### load CatBoosts

In [ ]:
saving_dir = "./checkpoints_MinMaxScaler_target/scalers"
saved_scalers = all_need_funcs.load_scalers(saving_dir)
# saved_scalers

In [ ]:
load_target_cbts = all_need_funcs.load_catboost_models("./checkpoints_MinMaxScaler_target/catboosts")

In [ ]:
load_diff_target_cbts = all_need_funcs.load_catboost_models("../checkpoints/catboosts_diff_target")

In [ ]:
standard_scaler_cbt_target_mape = all_need_funcs.eval_cbts_on_test(load_target_cbts, saved_scalers, test_df,
                                                                  do_pred_diff_target=False,
                                                                  #   do_scale=False,
                                                                  sleep_time=1,
                                                                  y_col='target')
standard_scaler_cbt_target_mape

In [ ]:
standard_scaler_cbt_diff_target_mape = all_need_funcs.eval_cbts_on_test(load_diff_target_cbts, saved_scalers, test_df,
                                                                        do_pred_diff_target=True,
                                                                        # do_scale=False,
                                                                        sleep_time=1,
                                                                        y_col='target')
standard_scaler_cbt_diff_target_mape

In [ ]:
make_prod_predict_by_cbt("SBER", loaded_models, saved_scalers, t_token=T_TOKEN)

In [ ]:
make_prod_predict_by_cbt("SBER", loaded_models, saved_scalers, t_token=T_TOKEN, is_diff_target=True)

##### SARIMAX

In [ ]:
# X_train.columns.tolist()
X_train, y_train
cur_sym = 'SBER'
cur_target_col = 'diff_target'

cur_train_df = train_df[train_df['Symbol'] == cur_sym]
cur_val_df = val_df[val_df['Symbol'] == cur_sym]
cur_test_df = test_df[test_df['Symbol'] == cur_sym]

X_train, y_train = data_funcs.create_X_y_df_from_df(cur_train_df, target_col=cur_target_col)
X_val, y_val = data_funcs.create_X_y_df_from_df(cur_val_df, target_col=cur_target_col)
X_test, y_test = data_funcs.create_X_y_df_from_df(cur_test_df, target_col=cur_target_col)

X_train.shape, y_train.shape, X_val.shape, y_val.shape, X_test.shape, y_test.shape

In [ ]:
# X_train

In [ ]:
train_endog = X_train['scaled_Close'].values
train_endog = y_train.values[-300:]
train_exog = X_train.drop(columns=['scaled_Close', 'Volume']).values.astype(float)[-300:]

test_endog = X_test['scaled_Close'].values
test_endog = y_test.values
test_exog = X_test.drop(columns=['scaled_Close', 'Volume']).values.astype(float)

type(train_endog.dtype), type(train_exog.dtype), type(test_endog.dtype), type(test_exog.dtype)

In [ ]:
plt.plot(train_endog)

In [ ]:
# 3. Определение параметров SARIMAX (p,d,q)(P,D,Q,s)
order = (3, 1, 1)          # Несезонные параметры (p, d, q)
seasonal_order = (1, 1, 1, 30)  # Сезонные параметры (P, D, Q, s) - например, 12 для месячных данных

# 4. Создание и обучение модели
model = SARIMAX(train_endog,
                exog=train_exog,
                order=order,
                seasonal_order=seasonal_order,
                enforce_stationarity=False,
                enforce_invertibility=False)

results = model.fit(disp=False)

In [ ]:
# 5. Вывод результатов
print(results.summary())

# 6. Прогнозирование
forecast_steps = len(test_endog)
forecast = results.get_forecast(steps=forecast_steps, exog=test_exog)
forecast_mean = forecast.predicted_mean

forecast_steps = len(train_endog)
train_forecast = results.get_forecast(steps=forecast_steps, exog=train_exog)
train_forecast_mean = train_forecast.predicted_mean

# 7. Визуализация
plt.figure(figsize=(12, 6))
plt.plot(cur_train_df['Date'][-len(train_endog):], train_endog, label='Train')
plt.plot(cur_train_df['Date'][-len(train_forecast_mean):], train_forecast_mean, label='Forecast', color='red')

plt.plot(cur_test_df['Date'], test_endog, label='Test')
plt.plot(cur_test_df['Date'], forecast_mean, label='Forecast', color='red')
plt.fill_between(cur_test_df['Date'],
                 forecast.conf_int()[:, 1],
                 forecast.conf_int()[:, 0],
                 color='pink', alpha=0.3)
plt.legend()
plt.show()

# 8. Оценка модели (например, MAPE)
mape = mean_absolute_percentage_error(test_endog, forecast_mean)
print(f'MAPE: {mape}')

In [ ]:
model = auto_arima(data, seasonal=True, m=7)  # m=7 для недельной сезонности
print(model.order, model.seasonal_order)

##### Prhophet

In [ ]:
# X_train.columns.tolist()
X_train, y_train
cur_sym = 'SBER'
cur_target_col = 'diff_target'

cur_train_df = train_df[train_df['Symbol'] == cur_sym]
cur_val_df = val_df[val_df['Symbol'] == cur_sym]
cur_test_df = test_df[test_df['Symbol'] == cur_sym]

phrophet_train_df = pd.concat([cur_train_df, cur_val_df])
phrophet_train_df = phrophet_train_df[["Date", "Close"]].rename(columns={"Date": "ds", "Close": "y"})
phrophet_train_df['ds'] = phrophet_train_df['ds'].dt.tz_localize(None)
phrophet_train_df = phrophet_train_df.iloc[-365:-200]
phrophet_train_df
# cur_test_df.set_index('Date')['Close']

In [ ]:

# Данные праздников
holidays = pd.DataFrame({
    "holiday": "dividend",
    "ds": pd.to_datetime(["2023-03-15", "2023-06-15"]),
    "lower_window": -2,
    "upper_window": 1,
})

# Создание модели
model = Prophet(
    changepoint_prior_scale=0.01,
    seasonality_prior_scale=0.1,
    changepoint_range=0.8,
    # holidays=holidays,
    seasonality_mode="multiplicative",  # Умножение сезонности на тренд
    # weekly_seasonality=True,
    yearly_seasonality=True,
)

# # Добавляем кастомную сезонность
# model.add_seasonality(
#     name="quarterly",
#     period=90,
#     fourier_order=5  # Учёт сложных квартальных колебаний
# )
# model.add_seasonality(
#     name="monthly",
#     period=30.5,
#     fourier_order=5
# )


# Обучение и прогноз
model.fit(phrophet_train_df)

In [ ]:
# Создание датафрейма для прогноза (на 30 дней вперед)
future = model.make_future_dataframe(periods=50)
forecast = model.predict(future)

# Визуализация
fig = model.plot(forecast)
plt.title("Прогноз цены акции с помощью Prophet")
plt.show()

# Компоненты прогноза (тренд, сезонность)
fig2 = model.plot_components(forecast)
plt.show()

In [ ]:
# test_forecast = forecast[forecast["ds"].isin(cur_test_df["Date"])]
future = model.make_future_dataframe(periods=1)
test_forecast = forecast
cur_test_df
test_forecast



last_cnt = 1000
plt.figure(figsize=(12, 6))
plt.plot(cur_test_df["Date"][-last_cnt:], cur_test_df['Close'][-last_cnt:], label="Фактические значения", color="blue")
plt.plot(test_forecast["ds"][-last_cnt:], test_forecast["yhat"][-last_cnt:], label="Прогноз Prophet", color="red", linestyle="--")
plt.fill_between(
    test_forecast["ds"][-last_cnt:],
    test_forecast["yhat_lower"][-last_cnt:],
    test_forecast["yhat_upper"][-last_cnt:],
    color="pink",
    alpha=0.3,
    label="Доверительный интервал",
)
plt.title("Прогноз vs Факт (тестовые данные)")
plt.xlabel("Дата")
plt.ylabel("Цена")
plt.legend()
plt.grid()
plt.show()


y_true = cur_test_df["Close"].values
y_pred = test_forecast["yhat"].values

# Расчет метрик
# mae = mean_absolute_error(y_true, y_pred)
# rmse = np.sqrt(mean_squared_error(y_true, y_pred))
mape = mean_absolute_percentage_error(y_true[-last_cnt:], y_pred[-last_cnt:])

# print(f"MAE: {mae:.2f}")
# print(f"RMSE: {rmse:.2f}")
print(f"MAPE: {mape:.2f}%")

#### LSTM

In [ ]:
import wandb
wandb.finish()
wandb.login()

##### обычный прогон

In [ ]:
cur_target_col = 'diff_target'
cur_target_col

In [ ]:
res_df.shape

In [ ]:
# Обучаем модель
print("Начинаем обучение модели...")
model, features_scalers = all_need_funcs.train_lstm_model(res_df,
                                        sequence_length=30,
                                        batch_size=64,
                                        # learning_rate=1e-1,
                                        max_epochs=50,
                                        #  embedding_dim: int = 32,
                                        hidden_dim = 256,
                                        num_layers = 5,
                                        # num_layers = 10,
                                        #  dropout=0.0,
                                        y_col=cur_target_col,
                                        train_start_date = "2021-01-01",
                                        accelerator='auto',
                                        wandb_name_iter=44)

In [ ]:
do_pred_diff_target = (cur_target_col == 'diff_target')
do_pred_diff_target

In [ ]:
lstm_predictions = all_need_funcs.eval_lstm_on_test_data(model, train_df,
                                                         scalers=scalers,
                                                         features_scalers=features_scalers,
                                                         do_pred_diff_target = do_pred_diff_target,
                                                        #  do_scale = True,
                                                         sleep_time = 1,
                                                         is_test_data = False
                                                         )

In [ ]:
val_df = res_df[(res_df['Date'] >= '2024-08-01') & (res_df['Date'] < '2025-01-01')]  # Последний год как тест
lstm_predictions = all_need_funcs.eval_lstm_on_test_data(model, val_df,
                                                         scalers=scalers,
                                                         features_scalers=features_scalers,
                                                         do_pred_diff_target = do_pred_diff_target,
                                                        #  do_scale = True,
                                                         is_test_data=False,
                                                         sleep_time = 1
                                                         )

In [ ]:
test_df = res_df[res_df['Date'] >= '2024-10-01']  # Последний год как тест
lstm_predictions = all_need_funcs.eval_lstm_on_test_data(model, test_df,
                                                         scalers=scalers,
                                                         features_scalers=features_scalers,
                                                         do_pred_diff_target = do_pred_diff_target,
                                                        #  do_scale = True,
                                                         sleep_time = 1
                                                         )

In [ ]:
model

In [ ]:
model_path = 'stock_lstm_StandardScaler_target_v3.pth'
model_path

In [ ]:
# do_pred_diff_target = False
# do_pred_diff_target

In [ ]:
import torch
# Сохранение модели StockLSTM
torch.save(model.state_dict(), model_path)  # Сохраняем только веса
# или полную модель:
# torch.save(model, 'stock_lstm_StandardScaler_diff_target.pth')

# from google.colab import files
# files.download(f"./{model_path}")


In [ ]:
# Создаем директорию для сохранения скейлеров, если она не существует
saving_dir = "./FeaturesScaler_diff_target/"
os.makedirs(saving_dir, exist_ok=True)

# Сохраняем каждый скейлер в отдельный файл
for ticker, scaler in scalers.items():
    scaler_path = f"{saving_dir}/{ticker}_scaler.pkl"
    if os.path.exists(scaler_path):
        os.remove(scaler_path)
    with open(scaler_path, 'wb') as f:
        pickle.dump(scaler, f)

!zip -r ./FeaturesScaler_diff_target.zip ./FeaturesScaler_diff_target

In [ ]:
load_model_path = model_path
# load_model_path = './stock_lstm_StandardScaler_diff_target_v2.pth'
load_model_path

In [ ]:
loaded_model = all_need_funcs.StockLSTM(feature_dim=139-32,
                                 n_symbols=12,
                                #  hidden_dim=128,
                                 hidden_dim=512,
                                 num_layers=5,
                                 embedding_dim=32)
loaded_model.load_state_dict(torch.load(load_model_path))
loaded_model.eval()

In [ ]:
lstm_predictions = all_need_funcs.eval_lstm_on_test_data(loaded_model, train_df,
                                                         scalers=scalers,
                                                         features_scalers=features_scalers,
                                                         do_pred_diff_target = do_pred_diff_target,
                                                        #  do_scale = True,
                                                         sleep_time = 2,
                                                         is_test_data = False
                                                         )

In [ ]:
test_df = res_df[res_df['Date'] >= '2024-10-01']  # Последний год как тест
lstm_predictions = all_need_funcs.eval_lstm_on_test_data(model, test_df,
                                                         scalers=scalers,
                                                         features_scalers=features_scalers,
                                                         do_pred_diff_target = do_pred_diff_target,
                                                        #  do_scale = True,
                                                         sleep_time = 1
                                                         )

#####  For in LSTM's hyperparams

In [ ]:
cur_target_col = 'diff_target'
print(f"{cur_target_col=}")

do_pred_diff_target = (cur_target_col == 'diff_target')
print(f"{do_pred_diff_target=}")

all_metrics_result = []
for cur_hidden_dim in tqdm([256]):
  for cur_num_layers in tqdm([5, 10, 15, 20]):
    for cur_lr in [1e-3]:
      for do_cut_train in [False, True]:
        cur_train_start_date = '2021-01-01' if do_cut_train else None
        # Обучаем модель
        print("Начинаем обучение модели...")
        model, features_scalers = all_need_funcs.train_lstm_model(res_df,
                                                sequence_length=30,
                                                batch_size=64,
                                                learning_rate=cur_lr,
                                                max_epochs=50,
                                                # max_epochs=3,
                                                #  embedding_dim: int = 32,
                                                hidden_dim=cur_hidden_dim,
                                                num_layers=cur_num_layers,
                                                y_col=cur_target_col,
                                                train_start_date=cur_train_start_date,
                                                # accelerator='auto',
                                                wandb_name_iter=45)


        lstm_predictions, train_metrics = all_need_funcs.eval_lstm_on_test_data(model, train_df,
                                                                scalers=scalers,
                                                                features_scalers=features_scalers,
                                                                do_pred_diff_target = do_pred_diff_target,
                                                                #  do_scale = True,
                                                                sleep_time = 1,
                                                                is_test_data = False,
                                                                do_return_metrics=True,
                                                                )

        test_df = res_df[res_df['Date'] >= '2024-10-01']  # Последний год как тест
        lstm_predictions, test_metrics = all_need_funcs.eval_lstm_on_test_data(model, test_df,
                                                                scalers=scalers,
                                                                features_scalers=features_scalers,
                                                                do_pred_diff_target = do_pred_diff_target,
                                                                #  do_scale = True,
                                                                do_return_metrics=True,
                                                                sleep_time = 1
                                                            )

        cur_metrics = {'lr':cur_lr, 'do_cut_train':do_cut_train,
                       'hidden_dim':cur_hidden_dim, 'num_layers':cur_num_layers,
                      'train_mse': train_metrics['mse'], 'train_mape': train_metrics['mape'],
                      'train_direct_accuracy': train_metrics['direct_accuracy'],
                      'test_mse': test_metrics['mse'], 'test_mape': test_metrics['mape'],
                      'test_direct_accuracy': test_metrics['direct_accuracy'],
                      }
        all_metrics_result.append(cur_metrics)

In [ ]:
all_metrics_result

In [ ]:
pd.DataFrame(all_metrics_result)

In [ ]:
pd.DataFrame(all_metrics_result).to_csv('all_lstm_metrics_v2_num_layers_WITH_diff_target.csv')

In [ ]:
# from google.colab import files
# files.download(f"./all_lstm_metrics_v2_num_layers.csv")

#####  Debug LSTM

In [ ]:
test_df = res_df[res_df['Date'] >= '2024-10-01']  # Последний год как тест
lstm_predictions = all_need_funcs.eval_lstm_on_test_data(model, test_df,
                                                         scalers=scalers,
                                                         features_scalers=features_scalers,
                                                         do_pred_diff_target = do_pred_diff_target,
                                                        #  do_scale = True,
                                                         sleep_time = 1
                                                         )

In [ ]:
# Создаем DataLoader'ы
train_loader, val_loader, test_loader, feature_dim, n_symbols = all_need_funcs.create_dataloaders(
    res_df, 30, 32
)


In [ ]:
len(val_loader.dataset.sequences)

In [ ]:
test_df.isna().sum().sum()
test_df['Date']

In [ ]:
test_dataset = all_need_funcs.StockDataset(test_df, sequence_length=30,
                                           max_sequences_per_symbol=1000,
                                           do_need_all_preds=True)


In [ ]:
seq_keys = test_dataset.sequences[934].keys()

symbols_hist = [cur_seq['symbol_idx'] for cur_seq in test_dataset.sequences]
# plt.hist(symbols_hist)
# plt.show()

dates_hist = [cur_seq['dates'] for cur_seq in test_dataset.sequences]
last_dates_hist = [cur_seq['dates'][-1] for cur_seq in test_dataset.sequences]
last_dates_hist
# for key in seq_keys:
#   print(key)
#   if key == 'symbol_idx':
#     print(f"{test_dataset.sequences[0][key]}\n")
#   else:
#     print(f"{len(test_dataset.sequences[0][key])}\n")


In [ ]:
lstm_predictions[lstm_predictions['Symbol'] == 'SBER'].tail(15)

In [ ]:
test_df[test_df['Symbol'] == 'SBER'].tail(15)

#### EnhancedStockLSTM

In [ ]:
import wandb
wandb.finish()
wandb.login()

##### обычный прогон


In [ ]:
cur_target_col = 'diff_target'
cur_target_col


In [ ]:
# Обучаем модель
print("Начинаем обучение модели...")
model, features_scalers = all_need_funcs.train_enhanced_lstm_model(res_df,
                                                 sequence_length=30,
                                                 batch_size=64,
                                                 max_epochs=50,
                                                 learning_rate=1e-4,
                                                 #  embedding_dim: int = 32,
                                                 hidden_dim = 256,
                                                 num_layers = 5,
                                                 #  num_layers = 1,
                                                 #  dropout=0.0,
                                                 y_col=cur_target_col,
                                                 train_start_date="2021-01-01",
                                                 wandb_name_iter=9)

In [ ]:
do_pred_diff_target = (cur_target_col == 'diff_target')
do_pred_diff_target

In [ ]:
lstm_predictions = all_need_funcs.eval_lstm_on_test_data(model, train_df,
                                                         scalers=scalers,
                                                         features_scalers=features_scalers,
                                                         do_pred_diff_target = do_pred_diff_target,
                                                        #  do_scale = True,
                                                         sleep_time = 1,
                                                         is_test_data = False
                                                         )

In [ ]:
val_df = res_df[(res_df['Date'] >= '2024-08-01') & (res_df['Date'] < '2025-01-01')]  # Последний год как тест
lstm_predictions = all_need_funcs.eval_lstm_on_test_data(model, val_df,
                                                         scalers=scalers,
                                                         features_scalers=features_scalers,
                                                         do_pred_diff_target = do_pred_diff_target,
                                                        #  do_scale = True,
                                                         is_test_data=False,
                                                         sleep_time = 1
                                                         )

In [ ]:
test_df = res_df[res_df['Date'] >= '2024-10-01']  # Последний год как тест
lstm_predictions = all_need_funcs.eval_lstm_on_test_data(model, test_df,
                                                         scalers=scalers,
                                                         features_scalers=features_scalers,
                                                         do_pred_diff_target = do_pred_diff_target,
                                                        #  do_scale = True,
                                                         sleep_time = 1
                                                         )

In [ ]:
model

In [ ]:
model_path = 'enhanced_lstm_StandardScaler_diff_target.pth'
model_path

In [ ]:
# do_pred_diff_target = False
do_pred_diff_target

In [ ]:
import torch
# Сохранение модели StockLSTM
torch.save(model.state_dict(), model_path)  # Сохраняем только веса


In [ ]:
# Создаем директорию для сохранения скейлеров, если она не существует
saving_dir = "./FeaturesScaler_diff_target/"
os.makedirs(saving_dir, exist_ok=True)

# Сохраняем каждый скейлер в отдельный файл
for ticker, scaler in scalers.items():
    scaler_path = f"{saving_dir}/{ticker}_scaler.pkl"
    if os.path.exists(scaler_path):
        os.remove(scaler_path)
    with open(scaler_path, 'wb') as f:
        pickle.dump(scaler, f)

!zip -r ./FeaturesScaler_diff_target.zip ./FeaturesScaler_diff_target

In [ ]:
load_model_path = model_path
# load_model_path = './stock_lstm_StandardScaler_diff_target_v2.pth'
load_model_path

In [ ]:
loaded_model = all_need_funcs.EnhancedStockLSTM(feature_dim=139-32,
                                                n_symbols=12,
                                                #  hidden_dim=128,
                                                hidden_dim=256,
                                                num_layers=5,
                                                embedding_dim=32)
loaded_model.load_state_dict(torch.load(load_model_path))
loaded_model.eval()

In [ ]:
lstm_predictions = all_need_funcs.eval_lstm_on_test_data(loaded_model, train_df,
                                                         scalers=scalers,
                                                         features_scalers=features_scalers,
                                                         do_pred_diff_target = do_pred_diff_target,
                                                        #  do_scale = True,
                                                         sleep_time = 1,
                                                         is_test_data = False
                                                         )

In [ ]:
test_df = res_df[res_df['Date'] >= '2024-10-01']  # Последний год как тест
lstm_predictions = all_need_funcs.eval_lstm_on_test_data(loaded_model, test_df,
                                                         scalers=scalers,
                                                         features_scalers=features_scalers,
                                                         do_pred_diff_target = do_pred_diff_target,
                                                        #  do_scale = True,
                                                         sleep_time = 1
                                                         )

##### For hyperparams

In [ ]:
cur_target_col = 'diff_target'
print(f"{cur_target_col=}")

do_pred_diff_target = (cur_target_col == 'diff_target')
print(f"{do_pred_diff_target=}")

all_metrics_result = []
for cur_hidden_dim in tqdm([512]):
  for cur_num_layers in tqdm([10]):
    for cur_sequence_length in tqdm([10, 20, 30, 60]):
      for cur_lr in [1e-3]:
        for do_cut_train in [False]:
          cur_train_start_date = '2021-01-01' if do_cut_train else None
          # Обучаем модель
          print("Начинаем обучение модели...")
          model, features_scalers = all_need_funcs.train_enhanced_lstm_model(res_df,
                                                  sequence_length=cur_sequence_length,
                                                  batch_size=64,
                                                  learning_rate=cur_lr,
                                                  max_epochs=50,
                                                  # max_epochs=3,
                                                  #  embedding_dim: int = 32,
                                                  hidden_dim=cur_hidden_dim,
                                                  num_layers=cur_num_layers,
                                                  y_col=cur_target_col,
                                                  train_start_date=cur_train_start_date,
                                                  # accelerator='auto',
                                                  wandb_name_iter=9)
          print(model)


          lstm_predictions, train_metrics = all_need_funcs.eval_lstm_on_test_data(model, train_df,
                                                                  scalers=scalers,
                                                                  features_scalers=features_scalers,
                                                                  sequence_length=cur_sequence_length,
                                                                  do_pred_diff_target = do_pred_diff_target,
                                                                  #  do_scale = True,
                                                                  sleep_time = 1,
                                                                  is_test_data = False,
                                                                  do_return_metrics=True,
                                                                  )

          test_df = res_df[res_df['Date'] >= '2024-10-01']  # Последний год как тест
          lstm_predictions, test_metrics = all_need_funcs.eval_lstm_on_test_data(model, test_df,
                                                                  sequence_length=cur_sequence_length,
                                                                  scalers=scalers,
                                                                  features_scalers=features_scalers,
                                                                  do_pred_diff_target = do_pred_diff_target,
                                                                  #  do_scale = True,
                                                                  do_return_metrics=True,
                                                                  sleep_time = 1
                                                              )

          cur_metrics = {'lr':cur_lr,
                        'do_cut_train':do_cut_train,
                         'sequence_length':cur_sequence_length,
                        'hidden_dim':cur_hidden_dim, 'num_layers':cur_num_layers,
                        'train_mse': train_metrics['mse'], 'train_mape': train_metrics['mape'],
                        'train_direct_accuracy': train_metrics['direct_accuracy'],
                        'test_mse': test_metrics['mse'], 'test_mape': test_metrics['mape'],
                        'test_direct_accuracy': test_metrics['direct_accuracy'],
                        }
          all_metrics_result.append(cur_metrics)

In [ ]:
all_metrics_result

In [ ]:
pd.DataFrame(all_metrics_result)

In [ ]:
pd.DataFrame(all_metrics_result).to_csv('all_enhanced_lstm_metrics_v5_seq_len_WITH_diff_target.csv')

##### For hyperparams WITH BIG_DF

In [ ]:
all_need_funcs.RUS_PROD_TICKERS_12

In [ ]:
sorted_assets = all_need_funcs.get_top_capitalized_assets(T_TOKEN, 1000, do_return_all=True)

In [ ]:
get_top_n_tickers = lambda n: [ticker_tup[0] for ticker_tup in sorted_assets[:n]]
tickers_dict = {
    "top 12" : all_need_funcs.RUS_PROD_TICKERS_12,
    "top 20" : get_top_n_tickers(20),
    "top 50" : get_top_n_tickers(50),
    "top 100" : get_top_n_tickers(100),
    "top 150" : get_top_n_tickers(150),
}
# sorted_assets
# tickers_dict["top 170"]

In [ ]:
big_df, big_scalers = all_need_funcs.create_featured_data_frame(all_need_funcs.get_symbol_data,
                                              interval="1d",
                                              token=T_TOKEN,
                                              symbols_list=tickers_dict["top 150"],
                                            #    symbols_list=["SBER", "YDEX", "T"],
                                              t_token=T_TOKEN,
                                              #  target_scaler='min-max'
                                              )


In [ ]:
big_df

In [ ]:
cur_target_col = 'diff_target'
print(f"{cur_target_col=}")

do_pred_diff_target = (cur_target_col == 'diff_target')
print(f"{do_pred_diff_target=}")

all_metrics_result = []
for top_n_name, top_n_value in tqdm(list(tickers_dict.items())[4:]):
  print(f"{top_n_name=}, {top_n_value=}")
  cur_big_df = big_df[big_df['Symbol'].isin(top_n_value)]
  print(f"{cur_big_df.shape=}")
  for cur_hidden_dim in tqdm([512]):
    for cur_num_layers in tqdm([10]):
      for cur_lr in [1e-3]:
        for do_cut_train in tqdm([False]):
          cur_train_start_date = '2021-01-01' if do_cut_train else None
          # Обучаем модель
          print("Начинаем обучение модели...")
          print(f"{top_n_name=}, {top_n_value=}")
          model, features_scalers = all_need_funcs.train_enhanced_lstm_model(cur_big_df,
                                                  sequence_length=30,
                                                  batch_size=64,
                                                  learning_rate=cur_lr,
                                                  max_epochs=30,
                                                  # max_epochs=3,
                                                  #  embedding_dim: int = 32,
                                                  hidden_dim=cur_hidden_dim,
                                                  num_layers=cur_num_layers,
                                                  y_col=cur_target_col,
                                                  train_start_date=cur_train_start_date,
                                                  # accelerator='auto',
                                                  wandb_name_iter=10)
          print(model)


          lstm_predictions, train_metrics = all_need_funcs.eval_lstm_on_test_data(model, train_df,
                                                                  scalers=big_scalers,
                                                                  features_scalers=features_scalers,
                                                                  do_pred_diff_target=do_pred_diff_target,
                                                                  #  do_scale = True,
                                                                  sleep_time = 1,
                                                                  is_test_data = False,
                                                                  do_return_metrics=True,
                                                                  )

          test_df = res_df[res_df['Date'] >= '2024-10-01']  # Последний год как тест
          lstm_predictions, test_metrics = all_need_funcs.eval_lstm_on_test_data(model, test_df,
                                                                  scalers=big_scalers,
                                                                  features_scalers=features_scalers,
                                                                  do_pred_diff_target = do_pred_diff_target,
                                                                  #  do_scale = True,
                                                                  do_return_metrics=True,
                                                                  sleep_time = 1
                                                              )

          cur_metrics = {'lr':cur_lr,
                          'top_n_tickers':top_n_name,
                          'do_cut_train':do_cut_train,
                          'hidden_dim':cur_hidden_dim, 'num_layers':cur_num_layers,
                          'train_mse': train_metrics['mse'], 'train_mape': train_metrics['mape'],
                          'train_direct_accuracy': train_metrics['direct_accuracy'],
                          'test_mse': test_metrics['mse'], 'test_mape': test_metrics['mape'],
                          'test_direct_accuracy': test_metrics['direct_accuracy'],
                        }
          all_metrics_result.append(cur_metrics)

In [ ]:
all_metrics_result

In [ ]:
pd.DataFrame(all_metrics_result)

In [ ]:
pd.DataFrame(all_metrics_result).to_csv('enhanced_lstm_metrics_v4_big_df_study_WITH_diff_target(3).csv')

#### Try Saved Models

##### Try CatBoosts

In [ ]:
saving_dir = "../checkpoints"
# do_pred_diff_target = True / False
# y_col = 'target' / 'diff_target'
do_pred_diff_target = (y_cal == 'diff_target')
do_pred_diff_target

In [ ]:
saved_scalers = all_need_funcs.load_scalers(f"{saving_dir}/scalers")
load_cbts = all_need_funcs.load_catboost_models(f"{saving_dir}/catboosts")

In [ ]:
standard_scaler_cbt_target_mape = all_need_funcs.eval_cbts_on_test(load_target_cbts, saved_scalers, test_df,
                                                    do_pred_diff_target=do_pred_diff_target,
                                                    #   do_scale=False,
                                                    sleep_time=1,
                                                    y_col='target')
standard_scaler_cbt_target_mape

##### Try LSTM

In [ ]:
cur_target_col = 'diff_target'
cur_target_col

do_pred_diff_target = (cur_target_col == 'diff_target')
do_pred_diff_target

In [ ]:
saved_scalers = all_need_funcs.load_scalers(f"{saving_dir}/scalers")
saved_features_scalers = all_need_funcs.load_scalers(f"./FeaturesScaler_diff_target")

In [ ]:
load_model_path = ''

In [ ]:
loaded_model = all_need_funcs.StockLSTM(feature_dim=139-32,
                                 n_symbols=12,
                                #  hidden_dim=128,
                                 hidden_dim=512,
                                 num_layers=5,
                                 embedding_dim=32)
loaded_model.load_state_dict(torch.load(load_model_path))
loaded_model.eval()

In [ ]:
test_df = res_df[res_df['Date'] >= '2024-10-01']  # Последний год как тест
lstm_predictions = all_need_funcs.eval_lstm_on_test_data(loaded_model, test_df,
                                                         scalers=scalers,
                                                         features_scalers=features_scalers,
                                                         do_pred_diff_target = do_pred_diff_target,
                                                        #  do_scale = True,
                                                         sleep_time = 1
                                                         )

##### Try EnhancedLSTM

In [ ]:
cur_target_col = 'diff_target'
cur_target_col

do_pred_diff_target = (cur_target_col == 'diff_target')
do_pred_diff_target

In [ ]:
saved_scalers = all_need_funcs.load_scalers(f"{saving_dir}/scalers")
saved_features_scalers = all_need_funcs.load_scalers(f"./FeaturesScaler_diff_target")

In [ ]:
load_model_path = ''

In [ ]:
loaded_model = all_need_funcs.EnhancedStockLSTM(feature_dim=139-32,
                                 n_symbols=12,
                                #  hidden_dim=128,
                                 hidden_dim=512,
                                 num_layers=5,
                                 embedding_dim=32)
loaded_model.load_state_dict(torch.load(load_model_path))
loaded_model.eval()

In [ ]:
test_df = res_df[res_df['Date'] >= '2024-10-01']  # Последний год как тест
lstm_predictions = all_need_funcs.eval_lstm_on_test_data(loaded_model, test_df,
                                                         scalers=scalers,
                                                         features_scalers=features_scalers,
                                                         do_pred_diff_target = do_pred_diff_target,
                                                        #  do_scale = True,
                                                         sleep_time = 1
                                                         )

#### Получить топ компаний по капитализации

In [ ]:
res = t_bank.get_top_capitalized_assets(T_TOKEN, 20)

In [ ]:
list(enumerate(res))